<a href="https://colab.research.google.com/github/MayerT1/Haleakal_NPS/blob/main/Haleakal_NPS_segmentation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<a href="https://githubtocolab.com/gee-community/geemap/blob/master/docs/notebooks/135_segmentation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open in Colab"/></a>

**Earth Engine Image Segmentation with the Segment Anything Model**

Uncomment the following line to install [geemap](https://geemap.org) if needed.

In [2]:
!pip install -U geemap

In [3]:
%pip install segment-geospatial pycrs

In [4]:
from samgeo import SamGeo

import ee
import geemap
import geemap.chart as chart
ee.Authenticate()
ee.Initialize(project='servir-sco-assets')
Map = geemap.Map()

In [5]:
from google.colab import drive
drive.mount('/content/drive/')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [6]:
import os

# Define the base project folder and subdirectories
base_dir = '/content/drive/Shareddrives/SCO-Shared/Science Resources/Thematic Service Areas/Ecosystem&CarbonManagement'
subdirs = [
    'Haleakal_NPS',

]

# Create each subdirectory
for subdir in subdirs:
    path = os.path.join(base_dir, subdir)
    os.makedirs(path, exist_ok=True)
    print(f"Created: {path}")


Created: /content/drive/Shareddrives/SCO-Shared/Science Resources/Thematic Service Areas/Ecosystem&CarbonManagement/Haleakal_NPS


# Block to grab NAIP for Hawaii does not need to be run every time

OCM Partners, 2025: 2021-2023 Hawaii NAIP 4-Band 8 Bit Imagery, https://www.fisheries.noaa.gov/inport/item/69406.
Full Citation Examples


https://coastalimagery.blob.core.windows.net/digitalcoast/HI_NAIP_2021_9668/index.html

In [20]:
import os
import requests
from tqdm import tqdm

# Base Google Drive path
base_dir = '/content/drive/Shareddrives/SCO-Shared/Science Resources/Thematic Service Areas/Ecosystem&CarbonManagement'
subdirs = [
    'Haleakal_NPS',
]

# Define NAIP tile names (you can modify this list as needed)
tiles = [
    "m_1815502_ne_05_060_20211217.tif",
    "m_1815503_nw_05_060_20211217.tif",
    "m_1815503_sw_05_060_20211217.tif",
    "m_1815504_nw_05_060_20211217.tif",
]

# Base URL for NAIP imagery
base_url = "https://coastalimagery.blob.core.windows.net/digitalcoast/HI_NAIP_2021_9668/"

# Create the full output directory
output_dir = os.path.join(base_dir, subdirs[0], 'naip_2021_tiles')
os.makedirs(output_dir, exist_ok=True)

# Download tiles
for tile in tqdm(tiles):
    url = base_url + tile
    out_path = os.path.join(output_dir, tile)
    if not os.path.exists(out_path):
        print(f"Downloading: {tile}")
        resp = requests.get(url, stream=True)
        if resp.status_code == 200:
            with open(out_path, 'wb') as f:
                for chunk in resp.iter_content(chunk_size=8192):
                    f.write(chunk)
        else:
            print(f"❌ Failed to download {tile} — HTTP {resp.status_code}")
    else:
        print(f"✅ Already exists: {tile}")


  0%|          | 0/4 [00:00<?, ?it/s]

Downloading: m_1815502_ne_05_060_20211217.tif


 25%|██▌       | 1/4 [00:26<01:20, 26.71s/it]

Downloading: m_1815503_nw_05_060_20211217.tif


 50%|█████     | 2/4 [00:48<00:47, 23.77s/it]

Downloading: m_1815503_sw_05_060_20211217.tif


 75%|███████▌  | 3/4 [01:13<00:24, 24.20s/it]

Downloading: m_1815504_nw_05_060_20211217.tif


100%|██████████| 4/4 [01:34<00:00, 23.63s/it]


In [7]:
!pip install leafmap

import leafmap

# Initialize interactive map (centered on your AOI)
m = leafmap.Map(center=[20.665, -156.175], zoom=13)

# Add each NAIP tile
tile_dir = '/content/drive/Shareddrives/SCO-Shared/Science Resources/Thematic Service Areas/Ecosystem&CarbonManagement/Haleakal_NPS/naip_2021_tiles'
tif_files = [
    "m_1815502_ne_05_060_20211217.tif",
    "m_1815503_nw_05_060_20211217.tif",
    "m_1815503_sw_05_060_20211217.tif",
    "m_1815504_nw_05_060_20211217.tif",
]

for tif in tif_files:
    m.add_raster(os.path.join(tile_dir, tif), layer_name=tif)

m


Map(center=[18.9687325, -155.5937815], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_tit…

dev

In [ ]:
# Map = geemap.Map()
# point = ee.Geometry.Point(-156.17605592238166,20.67994314028101)
# collection = (
#     ee.ImageCollection("USDA/NAIP/DOQQ")
#     .filterBounds(point)
#     .filterDate("2008-01-01", "2018-01-01")
#     .filter(ee.Filter.listContains("system:band_names", "N"))
# )
# image = collection.first()
# Map.addLayer(image, {}, "NAIP")
# Map.centerObject(point, 16)
# Map

In [ ]:
bbox = Map.user_roi_coords()
if bbox is None:
    bbox = [-156.19859354270451, 20.619830247838124, -156.15087167991155, 20.706403682807455] #[-122.2666, 37.8682, -122.252, 37.8752]


In [ ]:
geemap.ee_to_geotiff(
    image, "naip.tif", bbox, zoom=17, vis_params={"bands": ["R", "G", "B"]}
)

In [ ]:
sam = SamGeo(
    model_type="vit_h",
    checkpoint="sam_vit_h_4b8939.pth",
    device=None,
    sam_kwargs=None,
)

In [ ]:
sam.generate("naip.tif", output="masks.tif", foreground=True, unique=True)

In [ ]:
sam.show_masks(cmap="binary_r")

In [ ]:
sam.show_anns(axis="off", alpha=1, output="annotations.tif")

In [ ]:
Map.add_raster("annotations.tif", opacity=0.5, layer_name="Masks")
Map

In [ ]:
sam.tiff_to_vector("masks.tif", "masks.shp")

In [ ]:
style = {
    "color": "#3388ff",
    "weight": 2,
    "fillColor": "#7c4185",
    "fillOpacity": 0.5,
}
Map.add_vector("masks.shp", layer_name="Vector", style=style)
Map